In [26]:
import pandas as pd 
from collections import defaultdict
from itertools import chain

df = pd.read_csv('vocab_master_list.csv', names=['0'], header=None)


In [ ]:
from collections import defaultdict
from pathlib import Path
import pandas as pd 

my_dir_path = r"C:\Users\patel\OneDrive - iiit-b\Desktop\coursework\WSL Knowledge Graphs\codeBase\EduEmbedd\data\data_1_folder"

results = defaultdict(list)
for file in Path(my_dir_path).iterdir():
    with open(file, "r", encoding="utf8") as file_open:
        if(file.name[-3:]!="txt"):
            print(file.name)
            continue

        results["file_name"].append(file.name.split(".")[0])
        results["text"].append(file_open.read())
adf = pd.DataFrame(results)
adf.head()
adf

In [1]:
adf['course_name'] = adf.file_name.str.split('_').str[0]
adf['temp'] = adf.file_name.str.split('_').str[1]
adf['week'] = adf.temp.str.split('-').str[0]
adf['section'] = adf.temp.str.split('-').str[1]
adf['lesson'] = adf.temp.str.split('-').str[2]
adf['course_title'] = adf.file_name.str.split('_').str[2]
adf.dropna(inplace=True)

adf['week_no'] = adf['week'].str.extract('(\d+)', expand=False)
adf['week_no'] = adf['week_no'].astype(int)
adf['section_no'] = adf['section'].str.extract('(\d+)', expand=False)
adf['section_no'] = adf['section_no'].astype(int)
adf['lesson_no'] = adf['lesson'].str.extract('(\d+)', expand=False)
adf = adf.dropna()
adf['lesson_no'] = adf['lesson_no'].astype(int)

import re
adf['text'] = adf['text'].apply(lambda x: re.sub("\\n", " ",x))
adf['text'] = adf['text'].apply(lambda x: re.sub(r'\s+',' ', x))
adf['text'] = adf['text'].apply(lambda x: x.lower())

NameError: name 'adf' is not defined

In [ ]:
import string
string.punctuation
def remove_punct(text):
    text  = "".join([char for char in text if char not in string.punctuation])
    text = re.sub('[0-9]+', '', text)
    return text

adf['text'] = adf['text'].apply(lambda x: remove_punct(x))

import nltk
nltk.download('stopwords')
stopword = nltk.corpus.stopwords.words('english')
adf['text'] = adf['text'].apply(lambda x: ' '.join([word for word in x.split() if word not in (stopword)]))
# adf.head()
# stopwords 

ps = nltk.PorterStemmer()
def stemming(text):
    text = [ps.stem(word) for word in text]
    return text

adf['text1'] = adf['text'].apply(lambda x: ' '.join([ps.stem(word) for word in x.split()]))
adf.head(1)

In [ ]:
#We will not use nmf, instead will use lda
from sklearn.decomposition import NMF
from sklearn.feature_extraction.text import TfidfVectorizer
import numpy as np
def _calculate_nmf(text_list) :
    tfidf_vect = TfidfVectorizer()
    tfidf = tfidf_vect.fit_transform(text_list)
    # tfidf_feature_names = tfidf_vect.get_feature_names()
    # print(tfidf)
    nmf = NMF(n_components=15,random_state=1, alpha=.1, l1_ratio=.7, init='nndsvd').fit(tfidf)
    nmf_trans = nmf.transform(tfidf)
    print(nmf_trans)
    predicted_topics = [np.argsort(each)[::-1][0:5] for each in nmf_trans]
    return predicted_topics

adf['text_topics'] = _calculate_nmf(adf['text1'])

In [27]:
def complete(func):
    def wrapper(*args):
        print(f"{func.__name__}...", end='')
        ret_val = func(*args)
        print('done')
        return ret_val
    return wrapper

In [28]:
@complete
def load_data(path_to_master_list):
    df = pd.read_csv(path_to_master_list, names=['0'], header=None)
    mstr_list = list(set(df['0'].tolist()))
    mstr_list_clean = [vocab for vocab in mstr_list if str(vocab) != 'nan']
    
    separator = '_'
    word_list = [separator.join(word.split()) for word in mstr_list_clean]
    
    return mstr_list_clean, word_list

mstr_list_clean, mstr_list_clean_joined = load_data('vocab_master_list.csv')

load_data...done


In [23]:
len(mstr_list_clean_joined)

1881

In [29]:
@complete
def process_text(txt, v_list=mstr_list_clean):
    def _get_phrases(fle):
        phrase_dict = defaultdict(list)
        for line in map(str.rstrip, fle):
            k, _, phr = line.partition(" ")
            phrase_dict[k].append(line)
        return phrase_dict

    def _replace(text, dct):
        text1 = ""
        phrases = sorted(chain.from_iterable(dct[word] for word in text.split()
        if word in dct) ,reverse=1, key=len)
        mysetphrases = set(phrases)
        phrases = list(mysetphrases)
        for phr in phrases:
            text = text.replace(phr, phr.replace(" ", "_"))
        text1 =  "".join(text)
        return text1

    def _join_text(txt):
        text = _replace(txt, _get_phrases(v_list))
        return text

    return _join_text(txt)


In [30]:
mstr_list_clean[0]

'background'

In [31]:
@complete
def load_test_csv(path_to_test_csv):
    df = pd.read_csv(path_to_test_csv)
    return df

adf = load_test_csv('test.csv')

load_test_csv...done


In [32]:
process_text(adf['text'][0])

process_text...done


'okay welcome natural_language_processing name michael collins im professor computer_science columbia_university ive taught course several years recently columbia mit natural_language_processing think tremendously exciting field builds insights computer_science linguistics well see increasingly probability_statistics also huge impact daily lives many many applications technologies making use basic ideas natural_language_processing introductory lecture going cover basic points first question going ask natural_language_processing well discuss key applications nlp also key problems solved natural_language_processing second question well consider nlp_hard well consider key challenges well find natural_language_processing finally ill talk little bit course kind material well cover course general expect taking course high level natural_language_processing concerns use computers processing human natural languages one side problem often referred natural language_understanding take text input c

In [33]:
adf['join_text'] = adf['text'].apply(lambda x: process_text(x))

process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done
process_text...done


In [34]:
adf['join_text'][0]

'okay welcome natural_language_processing name michael collins im professor computer_science columbia_university ive taught course several years recently columbia mit natural_language_processing think tremendously exciting field builds insights computer_science linguistics well see increasingly probability_statistics also huge impact daily lives many many applications technologies making use basic ideas natural_language_processing introductory lecture going cover basic points first question going ask natural_language_processing well discuss key applications nlp also key problems solved natural_language_processing second question well consider nlp_hard well consider key challenges well find natural_language_processing finally ill talk little bit course kind material well cover course general expect taking course high level natural_language_processing concerns use computers processing human natural languages one side problem often referred natural language_understanding take text input c

In [35]:
import gensim
from gensim.models.coherencemodel import CoherenceModel
from gensim.models.ldamodel import LdaModel
from gensim.corpora.dictionary import Dictionary
from nltk.tokenize import RegexpTokenizer
import numpy as np

@complete
def docs_preprocessor(docs):
    tokenizer = RegexpTokenizer(r'\w+')
    for idx in range(len(docs)):
        docs[idx] = docs[idx].lower()  # Convert to lowercase.
        docs[idx] = tokenizer.tokenize(docs[idx])  # Split into words.

    # Remove numbers, but not words that contain numbers.
    docs = [[token for token in doc if not token.isdigit()] for doc in docs]
    
    # Remove words that are only one character.
    docs = [[token for token in doc if len(token) > 3] for doc in docs]
    
    # Lemmatize all words in documents.
    #lemmatizer = WordNetLemmatizer()
    #docs = [[lemmatizer.lemmatize(token) for token in doc] for doc in docs]
  
    return docs

text_list = adf['join_text'].to_list()
doc_tokens = docs_preprocessor(text_list)
dictionary = gensim.corpora.Dictionary(doc_tokens)
corpus = [
            dictionary.doc2bow(text) for text in doc_tokens
        ]
Lda = gensim.models.ldamodel.LdaModel
ldamodel = Lda(corpus, num_topics=15, id2word = dictionary, passes=20, iterations=400, chunksize = 500, eval_every = None,random_state=0)
id2word = dictionary

topics = []
for topic_num in range(0,14):
    topic = ldamodel.show_topic(topic_num, topn=60)
    
    topic = [list(t) for t in topic]
    topic = [[t[0],t[1],topic_num] for t in topic]
    #print(topic)
    topics.append(topic)

topics = [item for items in topics for item in items]   
tw_df = pd.DataFrame(topics, columns =['feature', 'proba', 'topic_num'])

def _calculate_lda(line):
    line = line.split()
    line_bow = id2word.doc2bow(line)
    doc_lda = ldamodel[line_bow]
    return([doc[0] for doc in doc_lda])


def _calculate_lda_p(line):
    line = line.split()
    line_bow = id2word.doc2bow(line)
    doc_lda = ldamodel[line_bow]
    return([(round(doc[1]*100,2)) for doc in doc_lda])
    

adf['l_text_topics'] = adf['join_text'].apply(lambda x: _calculate_lda(x))
adf['l_text_prob'] = adf['join_text'].apply(lambda x: _calculate_lda_p(x))

docs_preprocessor...done


In [36]:
tw_df.shape

(840, 3)

In [37]:
@complete
def cn_ci1(text):
    text_l = text.split()
    out_l = []
    for id, txt in enumerate(text_l):
        out = ['vi'+str(index) for index, word in enumerate(mstr_list_clean) if str(word) == str(txt)]
        out_l.append(out)
    out_l = [item for sublist in out_l for item in sublist]
    unique_out_l = []
    for x in out_l:
      if(x not in unique_out_l):
        unique_out_l.append(x)
    return unique_out_l

def concept_word(text):
    text_l = text.split()
    out_l = []
    for id, txt in enumerate(text_l):
        out = [word for index, word in enumerate(mstr_list_clean) if str(word) == str(txt)]
        out_l.append(out)
    out_l = [item for sublist in out_l for item in sublist]
    unique_out_l = []
    for x in out_l:
      if(x not in unique_out_l):
        unique_out_l.append(x)
    return unique_out_l

adf['concept_vocab_index'] = adf['join_text'].map(lambda s:cn_ci1(s))
adf['concept_vocab_word'] = adf['join_text'].map(lambda s:concept_word(s))

cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1...done
cn_ci1

In [38]:
@complete
def cn_ci(text):
    out = ['vi'+str(index) for index, word in enumerate(mstr_list_clean_joined) if str(word) == str(text)]
    return out

In [39]:
topics = []
for topic_num in range(0,14):
    topic = ldamodel.show_topic(topic_num, topn=100)
    
    topic = [list(t) for t in topic]
    topic = [[t[0],t[1],topic_num] for t in topic]
    topics.append(topic)
topics = [item for items in topics for item in items]   
tw_df = pd.DataFrame(topics, columns =['feature', 'proba', 'topic_num'])

In [40]:
tw_df.shape

(1400, 3)

In [41]:
tw_df['cv_index'] = tw_df['feature'].map(lambda s:cn_ci(s))

cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done
cn_ci...done

In [42]:
print(tw_df.shape)
tw_df1 = tw_df[tw_df['cv_index'].str.len() != 0]
tw_df1 = tw_df1.dropna()
print(tw_df1.shape)

(1400, 4)
(364, 4)


In [43]:
tw_df1.head(1)

feature     proba  topic_num  cv_index
0  example  0.020095          0  [vi1902]

In [44]:
tw_df1['cv_index_1'] = tw_df1['cv_index'].map(lambda s:s[0])
tw_df1.head()

feature     proba  topic_num  cv_index cv_index_1
0   example  0.020095          0  [vi1902]     vi1902
1  distance  0.012771          0   [vi771]      vi771
4     words  0.011305          0  [vi1334]     vi1334
5      word  0.009785          0   [vi698]      vi698
8      case  0.007331          0   [vi251]      vi251

In [45]:
tw_df1.to_csv("data_intermediates/tw_df1.csv")

In [46]:
from sklearn.feature_extraction.text import TfidfVectorizer
corpus = adf['join_text']
vectorizer = TfidfVectorizer(min_df=1)
X = vectorizer.fit_transform(corpus)
idf = vectorizer.idf_
print(vectorizer.get_feature_names())
#print( dict(zip(vectorizer.get_feature_names(), idf)))
def _feat(txt):
    print("****************************************************************************")
    response = vectorizer.transform([txt])
    feature_names = vectorizer.get_feature_names()
    arr = []
    for col in response.nonzero()[1]:
        if feature_names[col] in mstr_list_clean_joined:
            f_n = ['vi'+str(index) for index, word in enumerate(mstr_list_clean_joined) if word in feature_names[col]]
            arr.append([f_n[0], response[0, col]])
        else:
            f_n = 'NA'
        #print(feature_names[col], response[0, col])
        print(feature_names[col], response[0, col])
        print(f_n, response[0, col])
        print("=====")
        #arr.append([f_n, response[0, col]])
    return arr
adf['new'] = adf['join_text'].apply(lambda x: _feat(x))

['aa', 'aaai', 'aand', 'aardvark', 'ab', 'abbott', 'abbrevi', 'abbreviate', 'abbreviated', 'abbreviation', 'abbreviations', 'abc', 'abcba', 'abe', 'abil', 'abilities', 'ability', 'able', 'abner', 'abney', 'abneys', 'aboie', 'aboutbradvanced', 'aboutbrdifferent', 'aboutbrseven', 'aboutbrsmoothing', 'abrcandidate', 'abrdevelopment', 'abrdictionary', 'abrheld', 'abridged', 'abridgments', 'abrinaudible', 'abrlanguage_model', 'abrlot', 'abrnumber', 'abrprobability', 'abrpronunciation', 'abrrepresentation', 'abrset', 'abrtraining_corpus', 'abrvery', 'abrword', 'absence', 'absent', 'absolute', 'absolute_discounting', 'absolutely', 'absorb', 'abstract', 'abstracting', 'abstraction', 'abstractive', 'abstractly', 'abstractors', 'abstracts', 'ac', 'academics', 'accent', 'accented', 'accents', 'accept', 'acceptability', 'acceptable', 'acceptance', 'accepted', 'acceptor', 'access', 'accessing', 'accident', 'accolade', 'accommodate', 'accompanied', 'accompany', 'accomplish', 'accomplishments', 'acco

In [47]:
adf['course_no'] = adf['course_name'].str.extract('(\d+)', expand=False)
adf['course_no'] = adf['course_no'].astype(int)
adf['prerequisite'] = adf.groupby('course_no').file_name.shift(1)
adf['composite'] = adf.groupby('course_no').file_name.shift(-1)
adf.tail(1)

Unnamed: 0                                          file_name  \
296         301  Course3_W9-S1-L6_-_Sentence_Simplification_-_8...   

                                                  text course_name      temp  \
296  next segment going sentence simplification sen...     Course3  W9-S1-L6   

    week section lesson course_title  week_no  ...       text_topics  \
296   W9      S1     L6            -        9  ...  [ 4  0  2  3 14]   

                                             join_text    l_text_topics  \
296  next segment going sentence_simplification sen...  [5, 10, 11, 12]   

                     l_text_prob  \
296  [15.12, 13.03, 9.08, 62.57]   

                                   concept_vocab_index  \
296  [vi522, vi1556, vi340, vi1456, vi56, vi570, vi...   

                                    concept_vocab_word  \
296  [sentences, output, sentence, taking, research...   

                                                   new course_no  \
296  [[vi698, 0.013744252003344158], [vi378, 0.0125...         3   

                                          prerequisite composite  
296  Course3_W9-S1-L5_-_Summarization_Evaluation_-_...       NaN  

[1 rows x 23 columns]

In [48]:
adf.to_csv("data_intermediates/adf_pc_1.csv")

In [49]:
v2_df = pd.read_csv('data_intermediates/v2_df.csv')

In [50]:
v2_list_new = list(set(mstr_list_clean))
len(v2_list_new)

2071

In [51]:
@complete
def _calculate_tfidf(text_list):
    tfidf_vect = TfidfVectorizer()
    tfidf = tfidf_vect.fit_transform(text_list)
    df = pd.DataFrame(tfidf.todense(), columns = tfidf_vect.get_feature_names())
    # df = pd.DataFrame(tfidf[0].T.todense(), index=tfidf_vect.get_feature_names_out(), columns=["TF-IDF"])
    return df

temptfidf = _calculate_tfidf(adf['join_text'])
temptfidf

_calculate_tfidf...done


aa  aaai  aand  aardvark        ab  abbott  abbrevi  abbreviate  \
0    0.0   0.0   0.0       0.0  0.000000     0.0      0.0         0.0   
1    0.0   0.0   0.0       0.0  0.000000     0.0      0.0         0.0   
2    0.0   0.0   0.0       0.0  0.000000     0.0      0.0         0.0   
3    0.0   0.0   0.0       0.0  0.000000     0.0      0.0         0.0   
4    0.0   0.0   0.0       0.0  0.000000     0.0      0.0         0.0   
..   ...   ...   ...       ...       ...     ...      ...         ...   
292  0.0   0.0   0.0       0.0  0.000000     0.0      0.0         0.0   
293  0.0   0.0   0.0       0.0  0.000000     0.0      0.0         0.0   
294  0.0   0.0   0.0       0.0  0.000000     0.0      0.0         0.0   
295  0.0   0.0   0.0       0.0  0.025019     0.0      0.0         0.0   
296  0.0   0.0   0.0       0.0  0.000000     0.0      0.0         0.0   

     abbreviated  abbreviation  ...  zhao   zi      ziff  ziffs  zis  zones  \
0            0.0           0.0  ...   0.0  0.0  0.000000    0.0  0.0    0.0   
1            0.0           0.0  ...   0.0  0.0  0.000000    0.0  0.0    0.0   
2            0.0           0.0  ...   0.0  0.0  0.000000    0.0  0.0    0.0   
3            0.0           0.0  ...   0.0  0.0  0.000000    0.0  0.0    0.0   
4            0.0           0.0  ...   0.0  0.0  0.000000    0.0  0.0    0.0   
..           ...           ...  ...   ...  ...       ...    ...  ...    ...   
292          0.0           0.0  ...   0.0  0.0  0.000000    0.0  0.0    0.0   
293          0.0           0.0  ...   0.0  0.0  0.000000    0.0  0.0    0.0   
294          0.0           0.0  ...   0.0  0.0  0.000000    0.0  0.0    0.0   
295          0.0           0.0  ...   0.0  0.0  0.000000    0.0  0.0    0.0   
296          0.0           0.0  ...   0.0  0.0  0.067836    0.0  0.0    0.0   

     zoom  zue  zwarts   zz  
0     0.0  0.0     0.0  0.0  
1     0.0  0.0     0.0  0.0  
2     0.0  0.0     0.0  0.0  
3     0.0  0.0     0.0  0.0  
4     0.0  0.0     0.0  0.0  
..    ...  ...     ...  ...  
292   0.0  0.0     0.0  0.0  
293   0.0  0.0     0.0  0.0  
294   0.0  0.0     0.0  0.0  
295   0.0  0.0     0.0  0.0  
296   0.0  0.0     0.0  0.0  

[297 rows x 11674 columns]

In [52]:
cols = temptfidf.columns

cvw_tfidf_score = []
for i in range(len(temptfidf)):
  cvw = adf.loc[i]['concept_vocab_word']
  tfidf = temptfidf.loc[i]
  cvw_tfidf = []
  for word in cvw:
    for ind, col in enumerate(cols):
      if (word==col):
        cvw_tfidf.append(round(tfidf[ind],2))
  cvw_tfidf_score.append(cvw_tfidf)


adf['concept_vocab_word_tfidf'] = cvw_tfidf_score
adf.head()

Unnamed: 0                                          file_name  \
0           0         Course1_W1-S1-L1_Introduction_Part_1_11-17   
1           1         Course1_W1-S1-L2_Introduction_Part_2_10-28   
2           2  Course1_W1-S2-L1_Introduction_to_the_Language_...   
3           3  Course1_W1-S2-L2_Introduction_to_the_Language_...   
4           4      Course1_W1-S2-L3_Markov_Processes_Part_1_8-56   

                                                text course_name      temp  \
0  okay welcome natural language processing name ...     Course1  W1-S1-L1   
1  next want talk key challenges nlp answering qu...     Course1  W1-S1-L2   
2  okay first topic going cover course problem la...     Course1  W1-S2-L1   
3  soon start talk techniques solve precisely pro...     Course1  W1-S2-L2   
4  okay previous segments lecture gave basic defi...     Course1  W1-S2-L3   

  week section lesson  course_title  week_no  ...  \
0   W1      S1     L1  Introduction        1  ...   
1   W1      S1     L2  Introduction        1  ...   
2   W1      S2     L1  Introduction        1  ...   
3   W1      S2     L2  Introduction        1  ...   
4   W1      S2     L3        Markov        1  ...   

                                           join_text  l_text_topics  \
0  okay welcome natural_language_processing name ...  [5, 7, 8, 12]   
1  next want talk key challenges nlp answering qu...        [4, 12]   
2  okay first topic going cover course problem la...    [4, 11, 12]   
3  soon start talk techniques solve precisely pro...        [4, 12]   
4  okay previous segments lecture gave basic defi...        [4, 11]   

                  l_text_prob  \
0  [1.77, 6.22, 20.48, 71.43]   
1               [3.45, 96.42]   
2       [36.87, 41.03, 21.89]   
3                [36.5, 63.3]   
4              [78.48, 21.31]   

                                 concept_vocab_index  \
0  [vi1401, vi1630, vi1801, vi1239, vi1456, vi498...   
1  [vi1239, vi937, vi1085, vi1411, vi1116, vi883,...   
2  [vi1801, vi937, vi1193, vi79, vi1116, vi883, v...   
3  [vi675, vi16, vi937, vi1456, vi768, vi1691, vi...   
4  [vi85, vi1649, vi1801, vi882, vi2051, vi636, v...   

                                  concept_vocab_word  \
0  [linguistics, applications, first, question, t...   
1  [question, problem, ambiguity, time, natural, ...   
2  [first, problem, wide, range, natural, languag...   
3  [techniques, solve, problem, taking, input, re...   
4  [previous, trigram, first, markov, process, se...   

                                                 new course_no  \
0  [[vi698, 0.008740039496620137], [vi698, 0.0372...         1   
1  [[vi698, 0.033550652534270795], [vi698, 0.1119...         1   
2  [[vi698, 0.13110791712490455], [vi698, 0.03100...         1   
3  [[vi698, 0.025154494283644954], [vi1193, 0.041...         1   
4  [[vi698, 0.010191408844243216], [vi1084, 0.010...         1   

                                        prerequisite  \
0                                                NaN   
1         Course1_W1-S1-L1_Introduction_Part_1_11-17   
2         Course1_W1-S1-L2_Introduction_Part_2_10-28   
3  Course1_W1-S2-L1_Introduction_to_the_Language_...   
4  Course1_W1-S2-L2_Introduction_to_the_Language_...   

                                           composite  \
0         Course1_W1-S1-L2_Introduction_Part_2_10-28   
1  Course1_W1-S2-L1_Introduction_to_the_Language_...   
2  Course1_W1-S2-L2_Introduction_to_the_Language_...   
3      Course1_W1-S2-L3_Markov_Processes_Part_1_8-56   
4      Course1_W1-S2-L4_Markov_Processes_Part_2_6-28   

                            concept_vocab_word_tfidf  
0  [0.07, 0.18, 0.06, 0.03, 0.02, 0.02, 0.14, 0.0...  
1  [0.04, 0.08, 0.23, 0.02, 0.08, 0.09, 0.06, 0.0...  
2  [0.01, 0.08, 0.1, 0.04, 0.03, 0.23, 0.03, 0.05...  
3  [0.03, 0.03, 0.08, 0.03, 0.11, 0.04, 0.03, 0.0...  
4  [0.11, 0.08, 0.09, 0.04, 0.02, 0.17, 0.03, 0.0...  

[5 rows x 24 columns]

In [53]:
adf.to_csv('data_intermediates/adf_with_tfidf.csv')

In [54]:
adf1 = adf[['file_name','l_text_topics']]
adf1 = adf1.dropna()
adf1 = adf1.melt('file_name')
#df15 = df15.drop_duplicates(subset=['topics','variable','value'], keep='last')
adf1.rename(columns = {"file_name": "head"},  
          inplace = True) 
adf1.head(5)
print(adf1.shape)

adf1['prob'] = adf[['l_text_prob']]
adf1.head(5)

(297, 3)


head       variable  \
0         Course1_W1-S1-L1_Introduction_Part_1_11-17  l_text_topics   
1         Course1_W1-S1-L2_Introduction_Part_2_10-28  l_text_topics   
2  Course1_W1-S2-L1_Introduction_to_the_Language_...  l_text_topics   
3  Course1_W1-S2-L2_Introduction_to_the_Language_...  l_text_topics   
4      Course1_W1-S2-L3_Markov_Processes_Part_1_8-56  l_text_topics   

           value                        prob  
0  [5, 7, 8, 12]  [1.77, 6.22, 20.48, 71.43]  
1        [4, 12]               [3.45, 96.42]  
2    [4, 11, 12]       [36.87, 41.03, 21.89]  
3        [4, 12]                [36.5, 63.3]  
4        [4, 11]              [78.48, 21.31]

In [28]:
# import json
# adf1['value'] = adf1['value'].apply(lambda x:json.loads(x))
# adf1['prob'] = adf1['prob'].apply(lambda x:json.loads(x))
# type(adf1['prob'][0])
adf1 = adf1.explode(['value', 'prob'])
adf1['value'] = 'topic_' + adf1['value'].astype(str)
adf1.head(5)

head       variable     value   prob
0  Course1_W1-S1-L1_Introduction_Part_1_11-17  l_text_topics   topic_2  37.52
0  Course1_W1-S1-L1_Introduction_Part_1_11-17  l_text_topics   topic_5  15.98
0  Course1_W1-S1-L1_Introduction_Part_1_11-17  l_text_topics  topic_10  12.01
0  Course1_W1-S1-L1_Introduction_Part_1_11-17  l_text_topics  topic_12   4.02
0  Course1_W1-S1-L1_Introduction_Part_1_11-17  l_text_topics  topic_13  21.48

In [29]:
adf1.shape

(772, 4)

In [32]:
import ast
adf2 = adf[['file_name','concept_vocab_index']]
adf2 = adf2.dropna()
adf2 = adf2.melt('file_name')
adf2.rename(columns = {"file_name": "head"}, inplace = True) 
adf2['prob'] = adf['concept_vocab_word_tfidf']
# adf2['prob'] = adf2['prob'].apply(lambda x:ast.literal_eval(x) if x != [] else 0)
# adf2['value'] = adf2['value'].apply(lambda x:ast.literal_eval(x) if x != [] else 0)
print(len(adf2['prob'].iloc[0]), len(adf2['value'].iloc[0]))
adf2 = adf2.explode(['value','prob'])
adf2 = adf2.drop_duplicates(subset=['head','variable','value','prob'], keep='last')

adf2.head(5)

# type(adf2['value'][0])

20 20


head             variable   value  \
0  Course1_W1-S1-L1_Introduction_Part_1_11-17  concept_vocab_index  vi1793   
0  Course1_W1-S1-L1_Introduction_Part_1_11-17  concept_vocab_index  vi1139   
0  Course1_W1-S1-L1_Introduction_Part_1_11-17  concept_vocab_index    vi59   
0  Course1_W1-S1-L1_Introduction_Part_1_11-17  concept_vocab_index  vi1181   
0  Course1_W1-S1-L1_Introduction_Part_1_11-17  concept_vocab_index   vi529   

   prob  
0  0.07  
0  0.02  
0  0.02  
0  0.08  
0  0.03

In [31]:
adf2.shape

TypeError: object of type 'numpy.float64' has no len()

In [59]:
adf['prerequisite'] = adf['prerequisite'].fillna('start')
adf['composite'] = adf['composite'].fillna('end')
adf3 = adf[['file_name','prerequisite']]
adf3 = adf3.dropna()
adf3 = adf3.melt('file_name')
adf3.rename(columns = {"file_name": "head"}, inplace = True) 
adf3 = adf3.drop_duplicates(subset=['head','variable','value'], keep='last')
adf3.head()

head      variable  \
0         Course1_W1-S1-L1_Introduction_Part_1_11-17  prerequisite   
1         Course1_W1-S1-L2_Introduction_Part_2_10-28  prerequisite   
2  Course1_W1-S2-L1_Introduction_to_the_Language_...  prerequisite   
3  Course1_W1-S2-L2_Introduction_to_the_Language_...  prerequisite   
4      Course1_W1-S2-L3_Markov_Processes_Part_1_8-56  prerequisite   

                                               value  
0                                              start  
1         Course1_W1-S1-L1_Introduction_Part_1_11-17  
2         Course1_W1-S1-L2_Introduction_Part_2_10-28  
3  Course1_W1-S2-L1_Introduction_to_the_Language_...  
4  Course1_W1-S2-L2_Introduction_to_the_Language_...

In [60]:
adf4 = adf[['file_name']]
adf4['variable'] = 'level'
adf4['value'] = 'level_1'
adf4['value'] = adf4.apply(lambda row: 'level_1' if row['file_name'][6] == '1' else ('level_2' if row['file_name'][6] == '3' else 'level_3'), axis=1)
adf4.rename(columns = {"file_name": "head"}, inplace = True) 
adf4.head()

c:\Users\patel\anaconda3\envs\wsl_env\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
c:\Users\patel\anaconda3\envs\wsl_env\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
c:\Users\patel\anaconda3\envs\wsl_env\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try 

head variable    value
0         Course1_W1-S1-L1_Introduction_Part_1_11-17    level  level_1
1         Course1_W1-S1-L2_Introduction_Part_2_10-28    level  level_1
2  Course1_W1-S2-L1_Introduction_to_the_Language_...    level  level_1
3  Course1_W1-S2-L2_Introduction_to_the_Language_...    level  level_1
4      Course1_W1-S2-L3_Markov_Processes_Part_1_8-56    level  level_1

In [61]:
#topics to vacab have to be done separately
tw_df1 = pd.read_csv('tw_df1.csv')
adf5 = tw_df1[['topic_num','cv_index_1']]
adf5 = adf5.dropna()
adf5 = adf5.melt('topic_num')
adf5.rename(columns = {"topic_num": "head"}, inplace = True) 
adf5 = adf5.drop_duplicates(subset=['head','variable','value'], keep='last')
adf5['head'] = adf5['head'] + 1
adf5['head'] = 'topic_' + adf5['head'].astype(str)
adf5['variable'] = "concept_vocab_index"
adf5.head()

head             variable  value
0  topic_1  concept_vocab_index   vi62
1  topic_1  concept_vocab_index  vi491
2  topic_1  concept_vocab_index  vi493
3  topic_1  concept_vocab_index  vi823
4  topic_1  concept_vocab_index   vi47

In [62]:
adf5.shape

(181, 3)

In [63]:
fdf = pd.concat([adf1,adf2,adf3,adf4,adf5])
fdf = fdf.fillna(1)
fdf.head(4)

head       variable    value   prob
0  Course1_W1-S1-L1_Introduction_Part_1_11-17  l_text_topics  topic_0   2.03
0  Course1_W1-S1-L1_Introduction_Part_1_11-17  l_text_topics  topic_2  88.10
0  Course1_W1-S1-L1_Introduction_Part_1_11-17  l_text_topics  topic_4   9.77
1  Course1_W1-S1-L2_Introduction_Part_2_10-28  l_text_topics  topic_1   5.29

In [ ]:
fdf.to_csv('triples.csv ')

In [81]:
tst_df = pd.read_csv('v2_df.csv', index_col=[0])

In [85]:
import os

In [92]:
os.path.join(os.path.abspath('data_intermediates'), 'v2_df.csv')

'c:\\Users\\patel\\OneDrive - iiit-b\\Desktop\\coursework\\WSL Knowledge Graphs\\codeBase\\newCode\\code base\\code_2023_fall\\data\\data_intermediates\\v2_df.csv'

In [19]:
import pandas as pd
tst = pd.read_csv('data_intermediates/adf_with_tfidf.csv', index_col=[0])

In [20]:
adf = tst
tst.head(1)

Unnamed: 0.1                                   file_name  \
0             0  Course1_W1-S1-L1_Introduction_Part_1_11-17   

                                                text course_name      temp  \
0  okay welcome natural language processing name ...     Course1  W1-S1-L1   

  week section lesson  course_title  week_no  ...  \
0   W1      S1     L1  Introduction        1  ...   

                                           join_text  l_text_topics  \
0  okay welcome natural_language_processing name ...   [11, 12, 13]   

             l_text_prob                                concept_vocab_index  \
0  [18.82, 58.11, 22.96]  ['vi655', 'vi697', 'vi463', 'vi235', 'vi2006',...   

                                  concept_vocab_word  \
0  ['linguistics', 'applications', 'first', 'ques...   

                                                 new course_no prerequisite  \
0  [['vi180', 0.008800403837271098], ['vi180', 0....         1          NaN   

                                    composite  \
0  Course1_W1-S1-L2_Introduction_Part_2_10-28   

                            concept_vocab_word_tfidf  
0  [0.07, 0.18, 0.06, 0.03, 0.02, 0.02, 0.09, 0.0...  

[1 rows x 24 columns]

In [21]:
import ast
adf['l_text_prob'] = adf['l_text_prob'].apply(lambda x: ast.literal_eval(x))
adf['l_text_topics'] = adf['l_text_topics'].apply(lambda x: ast.literal_eval(x))

In [22]:
adf.head(1)

Unnamed: 0.1                                   file_name  \
0             0  Course1_W1-S1-L1_Introduction_Part_1_11-17   

                                                text course_name      temp  \
0  okay welcome natural language processing name ...     Course1  W1-S1-L1   

  week section lesson  course_title  week_no  ...  \
0   W1      S1     L1  Introduction        1  ...   

                                           join_text  l_text_topics  \
0  okay welcome natural_language_processing name ...   [11, 12, 13]   

             l_text_prob                                concept_vocab_index  \
0  [18.82, 58.11, 22.96]  ['vi655', 'vi697', 'vi463', 'vi235', 'vi2006',...   

                                  concept_vocab_word  \
0  ['linguistics', 'applications', 'first', 'ques...   

                                                 new course_no prerequisite  \
0  [['vi180', 0.008800403837271098], ['vi180', 0....         1          NaN   

                                    composite  \
0  Course1_W1-S1-L2_Introduction_Part_2_10-28   

                            concept_vocab_word_tfidf  
0  [0.07, 0.18, 0.06, 0.03, 0.02, 0.02, 0.09, 0.0...  

[1 rows x 24 columns]

In [25]:
adf[adf['l_text_prob'].apply(len) != adf['l_text_topics'].apply(len)]

Unnamed: 0.1                                          file_name  \
27            27  Course1_W2-S1-L2_Generative_Models_for_Supervi...   

                                                 text course_name      temp  \
27  last section described tagging problem describ...     Course1  W2-S1-L2   

   week section lesson course_title  week_no  ...  \
27   W2      S1     L2   Generative        2  ...   

                                            join_text  l_text_topics  \
27  last section described tagging problem describ...        [2, 13]   

             l_text_prob                                concept_vocab_index  \
27  [20.09, 1.01, 78.74]  ['vi889', 'vi1357', 'vi45', 'vi787', 'vi1027',...   

                                   concept_vocab_word  \
27  ['tagging', 'problem', 'learning', 'example', ...   

                                                  new course_no  \
27  [['vi416', 0.038779163945334705], ['vi1551', 0...         1   

                                  prerequisite  \
27  Course1_W2-S1-L1_The_Tagging_Problem_10-01   

                                            composite  \
27  Course1_W2-S1-L3_Hidden_Markov_Models_HMMs-_Ba...   

                             concept_vocab_word_tfidf  
27  [0.07, 0.03, 0.19, 0.08, 0.12, 0.24, 0.09, 0.0...  

[1 rows x 24 columns]

In [23]:
adf1 = adf[['file_name','l_text_topics']]
adf1 = adf1.dropna()
adf1 = adf1.melt('file_name')
adf1.rename(columns = {"file_name": "head"}, inplace = True) 
adf1['prob'] = adf[['l_text_prob']]
adf1 = adf1.explode(['value', 'prob'])
adf1['value'] = 'topic_' + adf1['value'].astype(str)

ValueError: columns must have matching element counts

In [3]:
import pandas as pd 

tst = pd.read_csv('triples.csv')
tst.head(1)

Unnamed: 0                                        head       variable  \
0           0  Course1_W1-S1-L1_Introduction_Part_1_11-17  l_text_topics   

     value   prob  
0  topic_6  13.13

In [4]:
from sklearn.preprocessing import MinMaxScaler

tst.drop_duplicates()
l_text_topics = tst[tst['variable']=='l_text_topics']
concept_vocab_index = tst[tst['variable']=='concept_vocab_index']
prerequisite = tst[tst['variable']=='prerequisite']
level = tst[tst['variable']=='level']


l_text_topics = l_text_topics.sample(frac=1)
concept_vocab_index = concept_vocab_index.sample(frac=1)
prerequisite = prerequisite.sample(frac=1)
level = level.sample(frac=1)

scaler = MinMaxScaler()
l_text_topics['prob'] = pd.DataFrame(scaler.fit_transform(pd.DataFrame(l_text_topics['prob'])), columns = ['prob'])

scaler = MinMaxScaler()
concept_vocab_index['prob'] = pd.DataFrame(scaler.fit_transform(pd.DataFrame(concept_vocab_index['prob'])), columns = ['prob'])

# scaler = StandardScaler()
# prerequisite['prob'] = pd.DataFrame(scaler.fit_transform(pd.DataFrame(prerequisite['prob'])), columns = ['prob'])

# scaler = StandardScaler()
# level['prob'] = pd.DataFrame(scaler.fit_transform(pd.DataFrame(level['prob'])), columns = ['prob'])

In [5]:
tst = pd.concat([l_text_topics, concept_vocab_index, prerequisite, level])

In [6]:
tst.head()

Unnamed: 0                                               head  \
460         175  Course2_W5-S3-L3_The_Exponential_Problem_in_Pa...   
136          49  Course1_W3-S2-L6_The_CKY_Parsing_Algorithm_Par...   
558         216  Course3_W1-S1-L1_-_Introduction_-_11_slides_08-39   
328         121         Course2_W1-S1-L1_Course_Introduction_14-11   
170          61  Course1_W5-S1-L4_Classical_Approaches_to_MT_Pa...   

          variable     value      prob  
460  l_text_topics  topic_12  0.312171  
136  l_text_topics  topic_10  0.336838  
558  l_text_topics   topic_2  0.998787  
328  l_text_topics   topic_2  0.355237  
170  l_text_topics   topic_2  0.057825

In [77]:
tst.drop('Unnamed: 0', axis=1, inplace=True)

In [76]:
tst.to_csv('triples_to_show.csv', index=False)